###  Imports:

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import contextily
import geopandas as gpd
from shapely.geometry import Point, Polygon
from geopy.geocoders import Nominatim
from tqdm import tqdm 
from decimal import *
import seaborn as sns


### Get existing schema from EC header

In [2]:
# Use only 1st row, header = None, so that we can use the header
#ec = pd.read_csv('Earth Challenge.csv',nrows=1,header = None)
#ecAr = pd.array(ec[1])
#print((ecAr[0]))

ec = pd.read_csv('Earth Challenge.csv',low_memory=False)
header = pd.array(ec.columns)
print(header)

<PandasArray>
[                              'X',                               'Y',
                        'OBJECTID',                'RecordSequenceID',
                        'UniqueID',                        'SourceID',
                  'LocationFreqID',                        'Location',
                         'Dataset',                    'Organization',
                           'Other',          'CountryName_FromSource',
        'SubCountry_L1_FromSource',        'SubCountry_L2_FromSource',
                      'Longitude1',                       'Latitude1',
                      'Longitude2',                       'Latitude2',
                    'TotalWidth_m',                   'TotalLength_m',
                  'TotalArea_Sq_m',                   'ShorelineName',
                  'WaterfrontName',              'BeachAreaLandcover',
                       'BeachType',                       'EventType',
                 'TotalVolunteers',                    'DateOri

### Open Literatti database

In [3]:
litter = pd.read_csv('USA OpenData Report Litterati.csv')
litter

Litter                                               Tags  \
0        1036458                                {bottlecap,plastic}   
1        1036624                                     {fork,plastic}   
2        1036449                                  {plastic,wrapper}   
3        1025933                                          {plastic}   
4        1025931                                          {tinfoil}   
...          ...                                                ...   
1877600     2402                                             {NULL}   
1877601     9281  {california,instagram,instapic,litter,macdonal...   
1877602    11653                                             {NULL}   
1877603    11654                                             {NULL}   
1877604  8152555                                     {aluminum,can}   

                              Location Country                    Date  
0        (-122.134176521,37.401654278)      US  2561-01-30 00:39:52+05  
1        (-122.134317937,37.401561979)      US  2561-01-30 00:39:30+05  
2        (-122.134848444,37.401673876)      US  2561-01-30 00:38:06+05  
3        (-122.134343237,37.399733858)      US  2561-01-24 23:47:00+05  
4        (-122.134468295,37.399795591)      US  2561-01-24 23:46:17+05  
...                                ...     ...                     ...  
1877600  (-122.268333435,37.867202758)      US  2012-07-02 04:15:40+05  
1877601  (-118.467994689,33.995864868)      US  2012-06-17 21:05:13+05  
1877602              (-97.4275,32.694)      US  2012-02-08 20:21:35+05  
1877603           (-97.42834,32.69316)      US  2012-01-20 07:31:49+05  
1877604      (-110.9632514,32.2797253)      US  2001-02-07 21:44:04+05  

[1877605 rows x 5 columns]

### ^^ Above we see that Latitude and Longitude are grouped together

## Functions getX(str) and getY(str)
### The functions take a string of the sort str = ('42.1889634352895/-71.8448098585561')
### getX gets rid of the parenthesis '()' and takes numbers until it reaches a comma ','
### returns: a string reprisenting Latitude 


In [4]:
def getX(str):
    
    x = ''
    for c in str:
        if (c == '('):
            continue
        elif (c == ','):
            break
        else:
            x += c
    return (x)

s = "(-97.4279,32.696)"
x = getX(s)
print(x)
print(type(x))


-97.4279
<class 'str'>


### getY gets rid of the parenthesis '()' and takes the numbers after it reaches a comma ','
### returns: a string reprisenting Longitude 

In [5]:
def getY(str):
    
    y = ''
    start = False
    for c in str:
        if(c == ','):
            start = True
            continue
        elif(start == True):
            if ((c != '(') & (c != ')')):
                y += c
                
            
    return (y)
st = "(-122.134176521,37.401654278)"
y = getY(st)
print(y)
print(type(y))


37.401654278
<class 'str'>


In [6]:
def getStr(str):
    x = ''
    for c in str:
        if ((c == '(') | (c == ')')):
            continue
        else:
            if(c == ','):
                x += c
                x += ' '
                continue
            x += c
    return x

s = "(-93.9228440915178,29.9566605873685)"
x = getStr(s)
print(x)
print(type(x))


-93.9228440915178, 29.9566605873685
<class 'str'>


In [7]:
# Make an array containing the location column
loc2020 = pd.array(litter['Location'])
tags = pd.array(litter['Tags'])
date = pd.array(litter['Date'])

latitude = []
longitude = []
counter = 0

for i in loc2020:
    
    latitude.append(getX(i))
    longitude.append(getY(i))

    counter += 1
    
    # Example Dataframe with coordinates, dates, tags
    # header[0] = 'X', header[1] = 'Y' 
    
dict = {"Date": date,"Tags": tags ,"X" : latitude, "Y" : longitude}
df = pd.DataFrame(dict)
df


Date  \
0        2561-01-30 00:39:52+05   
1        2561-01-30 00:39:30+05   
2        2561-01-30 00:38:06+05   
3        2561-01-24 23:47:00+05   
4        2561-01-24 23:46:17+05   
...                         ...   
1877600  2012-07-02 04:15:40+05   
1877601  2012-06-17 21:05:13+05   
1877602  2012-02-08 20:21:35+05   
1877603  2012-01-20 07:31:49+05   
1877604  2001-02-07 21:44:04+05   

                                                      Tags               X  \
0                                      {bottlecap,plastic}  -122.134176521   
1                                           {fork,plastic}  -122.134317937   
2                                        {plastic,wrapper}  -122.134848444   
3                                                {plastic}  -122.134343237   
4                                                {tinfoil}  -122.134468295   
...                                                    ...             ...   
1877600                                             {NULL}  -122.268333435   
1877601  {california,instagram,instapic,litter,macdonal...  -118.467994689   
1877602                                             {NULL}        -97.4275   
1877603                                             {NULL}       -97.42834   
1877604                                     {aluminum,can}    -110.9632514   

                    Y  
0        37.401654278  
1        37.401561979  
2        37.401673876  
3        37.399733858  
4        37.399795591  
...               ...  
1877600  37.867202758  
1877601  33.995864868  
1877602        32.694  
1877603      32.69316  
1877604    32.2797253  

[1877605 rows x 4 columns]

### It looks like a lot of the coordinates are pretty close together.
### Since in the EC dataset, each tuple is a cleanup EVENT, we can 
### group up litter by location ? How? ...I'm still figuring that out.


In [8]:
strLoc = []

for i in range(len(loc2020)):
    
    #strLoc.append(getStr(loc2020[i]))
    #print(getStr(loc2020[i]))
    strng = ("%s, %s" %(getY(loc2020[i]), getX(loc2020[i])))
    strLoc.append(strng)
    

df["Loc_str"] = strLoc
df

Date  \
0        2561-01-30 00:39:52+05   
1        2561-01-30 00:39:30+05   
2        2561-01-30 00:38:06+05   
3        2561-01-24 23:47:00+05   
4        2561-01-24 23:46:17+05   
...                         ...   
1877600  2012-07-02 04:15:40+05   
1877601  2012-06-17 21:05:13+05   
1877602  2012-02-08 20:21:35+05   
1877603  2012-01-20 07:31:49+05   
1877604  2001-02-07 21:44:04+05   

                                                      Tags               X  \
0                                      {bottlecap,plastic}  -122.134176521   
1                                           {fork,plastic}  -122.134317937   
2                                        {plastic,wrapper}  -122.134848444   
3                                                {plastic}  -122.134343237   
4                                                {tinfoil}  -122.134468295   
...                                                    ...             ...   
1877600                                             {NULL}  -122.268333435   
1877601  {california,instagram,instapic,litter,macdonal...  -118.467994689   
1877602                                             {NULL}        -97.4275   
1877603                                             {NULL}       -97.42834   
1877604                                     {aluminum,can}    -110.9632514   

                    Y                       Loc_str  
0        37.401654278  37.401654278, -122.134176521  
1        37.401561979  37.401561979, -122.134317937  
2        37.401673876  37.401673876, -122.134848444  
3        37.399733858  37.399733858, -122.134343237  
4        37.399795591  37.399795591, -122.134468295  
...               ...                           ...  
1877600  37.867202758  37.867202758, -122.268333435  
1877601  33.995864868  33.995864868, -118.467994689  
1877602        32.694              32.694, -97.4275  
1877603      32.69316           32.69316, -97.42834  
1877604    32.2797253      32.2797253, -110.9632514  

[1877605 rows x 5 columns]

In [244]:
geolocator = Nominatim(user_agent = "GMU")
addressLine = []

n = 0
pct = 0
for i in range(litter.size):
    
    l = geolocator.reverse(strLoc[i])
    addressLine.append(l)

    #l.raw("location")
    print(l)
    

Henry M. Gunn High School, Arastradero Road, Palo Alto, Santa Clara County, California, 94023, United States of America
Henry M. Gunn High School, Arastradero Road, Palo Alto, Santa Clara County, California, 94023, United States of America
Henry M. Gunn High School, Arastradero Road, Palo Alto, Santa Clara County, California, 94023, United States of America
Bol Park Bike Path, Palo Alto, Santa Clara County, California, 94023, United States of America
Bol Park Bike Path, Palo Alto, Santa Clara County, California, 94023, United States of America
Henry M. Gunn High School, Arastradero Road, Palo Alto, Santa Clara County, California, 94023, United States of America
Henry M. Gunn High School, Arastradero Road, Palo Alto, Santa Clara County, California, 94023, United States of America
Henry M. Gunn High School, Arastradero Road, Palo Alto, Santa Clara County, California, 94023, United States of America
Henry M. Gunn High School, Arastradero Road, Palo Alto, Santa Clara County, California, 94

Trossachs Boulevard Southeast, Tibbetts Station, Klahanie, Sammamish, King County, Washington, United States of America
Trossachs Boulevard Southeast, Tibbetts Station, Klahanie, Sammamish, King County, Washington, United States of America
Trossachs Boulevard Southeast, Tibbetts Station, Klahanie, Sammamish, King County, Washington, United States of America
Trossachs Boulevard Southeast, Tibbetts Station, Klahanie, Sammamish, King County, Washington, United States of America
Trossachs Boulevard Southeast, Tibbetts Station, Klahanie, Sammamish, King County, Washington, United States of America
Trossachs Boulevard Southeast, Tibbetts Station, Klahanie, Sammamish, King County, Washington, United States of America
Trossachs Boulevard Southeast, Tibbetts Station, Klahanie, Sammamish, King County, Washington, United States of America
Trossachs Boulevard Southeast, Tibbetts Station, Klahanie, Sammamish, King County, Washington, United States of America
Trossachs Boulevard Southeast, Tibbetts 

KeyboardInterrupt: 

In [9]:
### From google earth 0.001 is approximately 90 meters on the ground
### Figure out how to "package" tuples of litter according to how far appart they are
### If it's the same date, and within a 2km(figure out what that is in km) range of the previous entry
###

In [260]:


indexes1 = []
indexes2 = []

prevx1 = getX(next(litter.iterrows())[1]['Location'])
prevy1 = getY(next(litter.iterrows())[1]['Location'])

prevx2 = getX(next(litter.iterrows())[1]['Location'])
prevy2 = getY(next(litter.iterrows())[1]['Location'])

bool = False
for index, row in litter.iterrows():

    print("Current index = %d" %index)
    currx = getX(row['Location'])
    curry = getY(row['Location'])

    # if the current coordinates are close, keep going
    if( (abs(float(prevx1) - float(currx)) <= 1.0 ) and (abs(float(prevy1) - float(curry)) <= 1.0) ):
        
        indexes1.append(index)
        prevx1 = currx
        prevy1 = curry
        
        
    elif((abs(float(prevx2) - float(currx)) <= 1.0 ) and (abs(float(prevy2) - float(curry)) <= 1.0)):
        
        indexes2.append(index)
        prevx2 = currx
        prevy2 = curry
        
    #otherwise print start and end locations and form event from indexes
    else:
        if(bool):
            #change p1

            #print("Start index = %d, location = %s" %(startIdx1, litter.loc[startIdx1,'Location']))
            #print("End index = %d, location = %s" %(endIdx1-1, litter.loc[endIdx1-1,'Location']))
            
            print("p1: " + str(indexes1))
            formEvent(indexes1)
            indexes1 = []
            indexes1.append(index)
            prev1 = currx
            prev1 = curry
            bool = False
            
            
        else:
            
            print("p2: " + str(indexes2))
            formEvent(indexes2)
            indexes2 = []
            indexes2.append(index)
            prev2 = currx
            prev2 = curry
            
            bool = True
            

            

    

Current index = 0
Current index = 1
Current index = 2
Current index = 3
Current index = 4
Current index = 5
Current index = 6
Current index = 7
Current index = 8
Current index = 9
Current index = 10
Current index = 11
Current index = 12
Current index = 13
Current index = 14
Current index = 15
Current index = 16
Current index = 17
Current index = 18
Current index = 19
Current index = 20
Current index = 21
Current index = 22
Current index = 23
Current index = 24
p2: []
Current index = 25
p1: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23]
0 - 23
Current index = 26
p2: [24]
24 - 24
Current index = 27
p1: [25]
25 - 25
Current index = 28
p2: [26]
26 - 26
Current index = 29
p1: [27]
27 - 27
Current index = 30
p2: [28]
28 - 28
Current index = 31
p1: [29]
29 - 29
Current index = 32
p2: [30]
30 - 30
Current index = 33
p1: [31]
31 - 31
Current index = 34
p2: [32]
32 - 32
Current index = 35
p1: [33]
33 - 33
Current index = 36
p2: [34]
34 - 34
Current index =

Current index = 596
p2: [594]
594 - 594
Current index = 597
p1: [595]
595 - 595
Current index = 598
p2: [596]
596 - 596
Current index = 599
p1: [597]
597 - 597
Current index = 600
p2: [598]
598 - 598
Current index = 601
p1: [599]
599 - 599
Current index = 602
p2: [600]
600 - 600
Current index = 603
p1: [601]
601 - 601
Current index = 604
p2: [602]
602 - 602
Current index = 605
p1: [603]
603 - 603
Current index = 606
p2: [604]
604 - 604
Current index = 607
p1: [605]
605 - 605
Current index = 608
p2: [606]
606 - 606
Current index = 609
p1: [607]
607 - 607
Current index = 610
p2: [608]
608 - 608
Current index = 611
p1: [609]
609 - 609
Current index = 612
p2: [610]
610 - 610
Current index = 613
p1: [611]
611 - 611
Current index = 614
p2: [612]
612 - 612
Current index = 615
p1: [613]
613 - 613
Current index = 616
p2: [614]
614 - 614
Current index = 617
p1: [615]
615 - 615
Current index = 618
p2: [616]
616 - 616
Current index = 619
p1: [617]
617 - 617
Current index = 620
p2: [618]
618 - 618


Current index = 829
p1: [827]
827 - 827
Current index = 830
p2: [828]
828 - 828
Current index = 831
p1: [829]
829 - 829
Current index = 832
p2: [830]
830 - 830
Current index = 833
p1: [831]
831 - 831
Current index = 834
p2: [832]
832 - 832
Current index = 835
p1: [833]
833 - 833
Current index = 836
p2: [834]
834 - 834
Current index = 837
p1: [835]
835 - 835
Current index = 838
p2: [836]
836 - 836
Current index = 839
p1: [837]
837 - 837
Current index = 840
p2: [838]
838 - 838
Current index = 841
p1: [839]
839 - 839
Current index = 842
p2: [840]
840 - 840
Current index = 843
p1: [841]
841 - 841
Current index = 844
p2: [842]
842 - 842
Current index = 845
p1: [843]
843 - 843
Current index = 846
p2: [844]
844 - 844
Current index = 847
p1: [845]
845 - 845
Current index = 848
p2: [846]
846 - 846
Current index = 849
p1: [847]
847 - 847
Current index = 850
p2: [848]
848 - 848
Current index = 851
p1: [849]
849 - 849
Current index = 852
p2: [850]
850 - 850
Current index = 853
p1: [851]
851 - 851


p2: [1148]
1148 - 1148
Current index = 1151
p1: [1149]
1149 - 1149
Current index = 1152
p2: [1150]
1150 - 1150
Current index = 1153
p1: [1151]
1151 - 1151
Current index = 1154
p2: [1152]
1152 - 1152
Current index = 1155
p1: [1153]
1153 - 1153
Current index = 1156
p2: [1154]
1154 - 1154
Current index = 1157
p1: [1155]
1155 - 1155
Current index = 1158
p2: [1156]
1156 - 1156
Current index = 1159
p1: [1157]
1157 - 1157
Current index = 1160
p2: [1158]
1158 - 1158
Current index = 1161
p1: [1159]
1159 - 1159
Current index = 1162
p2: [1160]
1160 - 1160
Current index = 1163
p1: [1161]
1161 - 1161
Current index = 1164
p2: [1162]
1162 - 1162
Current index = 1165
p1: [1163]
1163 - 1163
Current index = 1166
p2: [1164]
1164 - 1164
Current index = 1167
p1: [1165]
1165 - 1165
Current index = 1168
p2: [1166]
1166 - 1166
Current index = 1169
p1: [1167]
1167 - 1167
Current index = 1170
p2: [1168]
1168 - 1168
Current index = 1171
p1: [1169]
1169 - 1169
Current index = 1172
p2: [1170]
1170 - 1170
Current i

p2: [1612]
1612 - 1612
Current index = 1615
p1: [1613]
1613 - 1613
Current index = 1616
p2: [1614]
1614 - 1614
Current index = 1617
p1: [1615]
1615 - 1615
Current index = 1618
p2: [1616]
1616 - 1616
Current index = 1619
p1: [1617]
1617 - 1617
Current index = 1620
p2: [1618]
1618 - 1618
Current index = 1621
p1: [1619]
1619 - 1619
Current index = 1622
p2: [1620]
1620 - 1620
Current index = 1623
p1: [1621]
1621 - 1621
Current index = 1624
p2: [1622]
1622 - 1622
Current index = 1625
p1: [1623]
1623 - 1623
Current index = 1626
p2: [1624]
1624 - 1624
Current index = 1627
p1: [1625]
1625 - 1625
Current index = 1628
p2: [1626]
1626 - 1626
Current index = 1629
p1: [1627]
1627 - 1627
Current index = 1630
p2: [1628]
1628 - 1628
Current index = 1631
p1: [1629]
1629 - 1629
Current index = 1632
p2: [1630]
1630 - 1630
Current index = 1633
p1: [1631]
1631 - 1631
Current index = 1634
p2: [1632]
1632 - 1632
Current index = 1635
p1: [1633]
1633 - 1633
Current index = 1636
p2: [1634]
1634 - 1634
Current i

...

Current index = 42550
p1: [42548]
42548 - 42548
Current index = 42551
p2: [42549]
42549 - 42549
Current index = 42552
p1: [42550]
42550 - 42550
Current index = 42553
p2: [42551]
42551 - 42551
Current index = 42554
p1: [42552]
42552 - 42552
Current index = 42555
p2: [42553]
42553 - 42553
Current index = 42556
p1: [42554]
42554 - 42554
Current index = 42557
p2: [42555]
42555 - 42555
Current index = 42558
p1: [42556]
42556 - 42556
Current index = 42559
p2: [42557]
42557 - 42557
Current index = 42560
p1: [42558]
42558 - 42558
Current index = 42561
p2: [42559]
42559 - 42559
Current index = 42562
p1: [42560]
42560 - 42560
Current index = 42563
p2: [42561]
42561 - 42561
Current index = 42564
p1: [42562]
42562 - 42562
Current index = 42565
p2: [42563]
42563 - 42563
Current index = 42566
p1: [42564]
42564 - 42564
Current index = 42567
p2: [42565]
42565 - 42565
Current index = 42568
p1: [42566]
42566 - 42566
Current index = 42569
p2: [42567]
42567 - 42567
Current index = 42570
p1: [42568]
42568 

Current index = 42886
p1: [42884]
42884 - 42884
Current index = 42887
p2: [42885]
42885 - 42885
Current index = 42888
p1: [42886]
42886 - 42886
Current index = 42889
p2: [42887]
42887 - 42887
Current index = 42890
p1: [42888]
42888 - 42888
Current index = 42891
p2: [42889]
42889 - 42889
Current index = 42892
p1: [42890]
42890 - 42890
Current index = 42893
p2: [42891]
42891 - 42891
Current index = 42894
p1: [42892]
42892 - 42892
Current index = 42895
p2: [42893]
42893 - 42893
Current index = 42896
p1: [42894]
42894 - 42894
Current index = 42897
p2: [42895]
42895 - 42895
Current index = 42898
p1: [42896]
42896 - 42896
Current index = 42899
p2: [42897]
42897 - 42897
Current index = 42900
p1: [42898]
42898 - 42898
Current index = 42901
p2: [42899]
42899 - 42899
Current index = 42902
p1: [42900]
42900 - 42900
Current index = 42903
p2: [42901]
42901 - 42901
Current index = 42904
p1: [42902]
42902 - 42902
Current index = 42905
p2: [42903]
42903 - 42903
Current index = 42906
p1: [42904]
42904 

Current index = 43225
p1: [43223]
43223 - 43223
Current index = 43226
p2: [43224]
43224 - 43224
Current index = 43227
p1: [43225]
43225 - 43225
Current index = 43228
p2: [43226]
43226 - 43226
Current index = 43229
p1: [43227]
43227 - 43227
Current index = 43230
p2: [43228]
43228 - 43228
Current index = 43231
p1: [43229]
43229 - 43229
Current index = 43232
p2: [43230]
43230 - 43230
Current index = 43233
p1: [43231]
43231 - 43231
Current index = 43234
p2: [43232]
43232 - 43232
Current index = 43235
p1: [43233]
43233 - 43233
Current index = 43236
p2: [43234]
43234 - 43234
Current index = 43237
p1: [43235]
43235 - 43235
Current index = 43238
p2: [43236]
43236 - 43236
Current index = 43239
p1: [43237]
43237 - 43237
Current index = 43240
p2: [43238]
43238 - 43238
Current index = 43241
p1: [43239]
43239 - 43239
Current index = 43242
p2: [43240]
43240 - 43240
Current index = 43243
p1: [43241]
43241 - 43241
Current index = 43244
p2: [43242]
43242 - 43242
Current index = 43245
p1: [43243]
43243 

Current index = 43593
p1: [43591]
43591 - 43591
Current index = 43594
p2: [43592]
43592 - 43592
Current index = 43595
p1: [43593]
43593 - 43593
Current index = 43596
p2: [43594]
43594 - 43594
Current index = 43597
p1: [43595]
43595 - 43595
Current index = 43598
p2: [43596]
43596 - 43596
Current index = 43599
p1: [43597]
43597 - 43597
Current index = 43600
p2: [43598]
43598 - 43598
Current index = 43601
p1: [43599]
43599 - 43599
Current index = 43602
p2: [43600]
43600 - 43600
Current index = 43603
p1: [43601]
43601 - 43601
Current index = 43604
p2: [43602]
43602 - 43602
Current index = 43605
p1: [43603]
43603 - 43603
Current index = 43606
p2: [43604]
43604 - 43604
Current index = 43607
p1: [43605]
43605 - 43605
Current index = 43608
p2: [43606]
43606 - 43606
Current index = 43609
p1: [43607]
43607 - 43607
Current index = 43610
p2: [43608]
43608 - 43608
Current index = 43611
p1: [43609]
43609 - 43609
Current index = 43612
p2: [43610]
43610 - 43610
Current index = 43613
p1: [43611]
43611 

KeyboardInterrupt: 

In [256]:
#Takes 2 indexes from litterati, then prints their locations, along with the difference in Xs and Ys

def checkLocations(index1,index2):

    print(geolocator.reverse(("%s, %s" %(getY(litter.loc[index1,'Location']), getX(litter.loc[index1,'Location'])))))
    print(geolocator.reverse(("%s, %s" %(getY(litter.loc[index2,'Location']), getX(litter.loc[index2,'Location'])))))
    print("The difference in X: %f, Index: %d" %(abs(float(getX(litter.loc[index1,'Location'])) - float(getX(litter.loc[index2,'Location']))),index2))
    print("The difference in Y: %f" %(abs(float(getY(litter.loc[index1,'Location'])) - float(getY(litter.loc[index2,'Location'])))))
for i in range(26,100,1):
    
    checkLocations(25,i)
    
    

259, Northwest 11th Street, Rainbow Homes, Delray Beach, Palm Beach County, Florida, 33444, United States of America
198, Northeast 9th Street, Rainbow Homes, Delray Beach, Palm Beach County, Florida, 33444, United States of America
The difference in X: 0.004843, Index: 26
The difference in Y: 0.001724
259, Northwest 11th Street, Rainbow Homes, Delray Beach, Palm Beach County, Florida, 33444, United States of America
835, Northeast 2nd Avenue, Tropic Isle, Delray Beach, Palm Beach County, Florida, 33444, United States of America
The difference in X: 0.004952, Index: 27
The difference in Y: 0.002256
259, Northwest 11th Street, Rainbow Homes, Delray Beach, Palm Beach County, Florida, 33444, United States of America
Hacker Dermatology, 226, Palm Court, Tropic Isle, Delray Beach, Palm Beach County, Florida, 33444, United States of America
The difference in X: 0.005448, Index: 28
The difference in Y: 0.002685
259, Northwest 11th Street, Rainbow Homes, Delray Beach, Palm Beach County, Florid

259, Northwest 11th Street, Rainbow Homes, Delray Beach, Palm Beach County, Florida, 33444, United States of America
373, Northeast 5th Avenue, Tropic Isle, Delray Beach, Palm Beach County, Florida, 33483, United States of America
The difference in X: 0.008215, Index: 53
The difference in Y: 0.007932
259, Northwest 11th Street, Rainbow Homes, Delray Beach, Palm Beach County, Florida, 33444, United States of America
333, Northeast 5th Avenue, Tropic Isle, Delray Beach, Palm Beach County, Florida, 33483, United States of America
The difference in X: 0.008227, Index: 54
The difference in Y: 0.008700
259, Northwest 11th Street, Rainbow Homes, Delray Beach, Palm Beach County, Florida, 33444, United States of America
349, Northeast 5th Avenue, Tropic Isle, Delray Beach, Palm Beach County, Florida, 33483, United States of America
The difference in X: 0.007922, Index: 55
The difference in Y: 0.008407
259, Northwest 11th Street, Rainbow Homes, Delray Beach, Palm Beach County, Florida, 33444, Un

KeyboardInterrupt: 

In [254]:
first = 25
second = 26
checkLocations(first,second)
print("The difference: %f - %f = %f" %(abs(float(getX(litter.loc[first,'Location']))), abs(float(getX(litter.loc[second,'Location']))),abs(abs(float(getX(litter.loc[first,'Location']))) - abs(float(getX(litter.loc[second,'Location']))))))

259, Northwest 11th Street, Rainbow Homes, Delray Beach, Palm Beach County, Florida, 33444, United States of America
198, Northeast 9th Street, Rainbow Homes, Delray Beach, Palm Beach County, Florida, 33444, United States of America
The difference in X: 0.004843, Index: 26
The difference in Y: 0.001724
The difference: 80.075916 - 80.071072 = 0.004843


In [213]:
def formEvent(indexes):
    
    if(indexes == []):
        pass
    else:
        
        print("%d - %d" %(indexes[0],indexes[-1]))
        #for i in indexes:
            #print(i)
        new_row = {
            "X": getX(litter.loc[indexes[0],'Location']),
            "Y": getY(litter.loc[indexes[0],'Location']),
            "Dataset": "Litterati",
            "Organization": "Litterati App User",
            "SUM_Hard_PlasticBeverageBottle": 0,
            "SUM_Hard_OtherPlasticBottle": 0,
            "SUM_HardOrSoft_PlasticBottleCap": 0,
            "SUM_Other_PlasticOrFoamFoodContainer": 0,
            "SUM_Hard_BucketOrCrate": 0,
            "SUM_Hard_Lighter": 0,
            "SUM_OtherHardPlastic": 0,
            "SUM_PlasticOrFoamPlatesBowlsCup": 0,
            "SUM_HardSoft_PersonalCareProduc": 0,
            "SUM_Hard_LollipopStick_EarBu": 0,
            "SUM_Soft_Bag": 0,
            "SUM_Soft_WrapperOrLabel": 0,
            "SUM_Soft_Straw": 0,
            "SUM_Soft_OtherPlastic": 0,
            "SUM_Soft_CigaretteButts": 0,
            "SUM_Other_StringRingRibbon": 0,
            "SUM_Other_Net": 0,
            "SUM_Other_FishingLineLureRope": 0,
            "SUM_Other_BuoysAndFloats": 0,
            "SUM_Foam_OtherPlasticDebris": 0,
            "SUM_Other_OtherPlasticDebris": 0,
            "SUM_Soft_sheets": 0,
            "SUM_Other_StrapsTiesBands": 0,
            "SUM_Other_Glowsticks": 0,
            "SUM_OtherFishing": 0
        }



        abs(float(getX(litter.loc[23,'Location'])) - float(getX(litter.loc[25,'Location']))))

In [199]:
formEvent([760,761,762,763,764,765])

760
761
762
763
764
765


In [19]:
unique_labels = litter[["Tags"]].drop_duplicates(subset = ["Tags"])
unique_labels

            

Tags
0                                      {bottlecap,plastic}
1                                           {fork,plastic}
2                                        {plastic,wrapper}
3                                                {plastic}
4                                                {tinfoil}
...                                                    ...
1877396                                 {camel,smokekills}
1877401                                            {lance}
1877411                                            {lorna}
1877539                                  {rolledgoldbrand}
1877601  {california,instagram,instapic,litter,macdonal...

[90699 rows x 1 columns]

In [32]:
unique_labels_df = litter[["Tags"]].drop_duplicates(subset = ["Tags"])
#unique_labels_df
unique_labels = pd.array(unique_labels_df['Tags'])
#print(type(unique_labels))
unique_labels_df

Tags
0                                      {bottlecap,plastic}
1                                           {fork,plastic}
2                                        {plastic,wrapper}
3                                                {plastic}
4                                                {tinfoil}
...                                                    ...
1877396                                 {camel,smokekills}
1877401                                            {lance}
1877411                                            {lorna}
1877539                                  {rolledgoldbrand}
1877601  {california,instagram,instapic,litter,macdonal...

[90699 rows x 1 columns]

In [ ]:
str = "Bottleasctgt"
if ("bottle" or "can") in str.lower():
    print("hyea")

In [ ]:
for index, row in unique_labels.iterrows():
    
    if "plastic" in row["Tags"]: 
        
        if ("bottle" or "can") in row["Tags"].lower():
            #Do what?

In [148]:
value_counts = pd.DataFrame(litter[["Tags"]].value_counts())



<PandasArray>
[0]
Length: 1, dtype: int64

In [153]:
tags = []
counts = []
idx = 0
for index, row in value_counts.iterrows():
    
    tags.append(index[0])
    counts.append(row[0])
    
       



In [166]:
percentage_plastic = []
plastic_indexes = []
percentage = 0
for i in range(len(tags)):
   
    if("plastic" in tags[i].lower()):
        
        plastic_indexes.append(i)
        
    elif("foam" in tags[i].lower()):
        
        plastic_indexes.append(i)
        
    elif(("bucket" in tags[i].lower()) or 
         ("crate" in tags[i].lower()) or
         ("lighter" in tags[i].lower()) or
         ("cigarette" in tags[i].lower()) or
         ("straw" in tags[i].lower()) or
         ("crate" in tags[i].lower())
        
        )
for i in plastic_indexes:
    percentage += counts[i]/1877605 


In [168]:
len(plastic_indexes)

31651

In [174]:
from datetime import datetime
import os

import pandas as pd


raw_data = pd.read_csv('USA OpenData Report Litterati.csv')

LIT_PLASTIC_MAPPINGS = {
    ("CLOTH", "Buoys and floats") : "SUM_Other_BuoysAndFloats",
    ("CLOTH", "Fishing Gear") : "SUM_Other_FishingLineLureRope",
    ("CLOTH", "Fishing Net") : "SUM_Other_Net",
    ("CLOTH", "Fishing Traps") : "SUM_OtherFishing",
    ("CLOTH", "Fishing lures and lines") : "SUM_Other_FishingLineLureRope",
    ("CLOTH", "Lobster Claw Bands") : "SUM_OtherFishing",
    ("CLOTH", "Other Fishing Gear") : "SUM_OtherFishing",
    ("CLOTH", "Plastic Rope or Net") : "SUM_Other_Net",
    ("OTHER ITEMS", "Bait Containers") : "SUM_OtherHardPlastic",
    ("OTHER ITEMS", "Bulk Bags") : "SUM_Soft_Bag",
    ("OTHER ITEMS", "Condoms") : "SUM_HardSoft_PersonalCareProduc",
    ("OTHER ITEMS", "Feminine Hygeine Products") : "SUM_HardSoft_PersonalCareProduc",
    ("OTHER ITEMS", "Foam or Plastic Take Out Containers") : "SUM_Other_PlasticOrFoamFoodContainer",
    ("OTHER ITEMS", "Industrial or Chemical Plastic Packaging") : "SUM_Other_OtherPlasticDebris",
    ("OTHER ITEMS", "Other Plastic") : "SUM_Other_OtherPlasticDebris",
    ("OTHER ITEMS", "Other Plastic Packaging") : "SUM_Other_OtherPlasticDebris",
    ("OTHER ITEMS", "Plastic Film") : "SUM_Soft_WrapperOrLabel",
    ("OTHER ITEMS", "Plastic Food Containers") : "SUM_Other_PlasticOrFoamFoodContainer",
    ("OTHER ITEMS", "Plastic Piping") : "SUM_Other_OtherPlasticDebris",
    ("OTHER ITEMS", "Plastic Sheeting or Tarps") : "SUM_Soft_sheets",
    ("OTHER ITEMS", "Plastic Shipping Waste") : "SUM_Other_OtherPlasticDebris",
    ("OTHER ITEMS", "Plastic String") : "SUM_Other_StringRingRibbon",
    ("OTHER ITEMS", "Styrofoam Packaging") : "SUM_Foam_OtherPlasticDebris",
    ("OTHER ITEMS", "Syringes") : "SUM_Other_OtherPlasticDebris",
    ("PLASTIC", "Aquaculture Gear") : "SUM_Other_OtherPlasticDebris",
    ("PLASTIC", "Balloon and/or String") : "SUM_Other_StringRingRibbon",
    ("PLASTIC", "Cigarettes/Cigars") : "SUM_Soft_CigaretteButts",
    ("PLASTIC", "Fishing Line") : "SUM_Other_FishingLineLureRope",
    ("PLASTIC", "Foam Fragment") : "SUM_Foam_OtherPlasticDebris",
    ("PLASTIC", "Foam or Plastic Cups or Plates") : "SUM_PlasticOrFoamPlatesBowlsCup",
    ("PLASTIC", "Other Plastic Jugs") : "SUM_Hard_OtherPlasticBottle",
    ("PLASTIC", "Other Rubber Items") : "SUM_Other_OtherPlasticDebris",
    ("PLASTIC", "Personal Care Products") : "SUM_HardSoft_PersonalCareProduc",
    ("PLASTIC", "Plastic Bags") : "SUM_Soft_Bag",
    ("PLASTIC", "Plastic Bottle") : "SUM_Hard_PlasticBeverageBottle",
    ("PLASTIC", "Plastic Caps or Lids") : "SUM_HardOrSoft_PlasticBottleCap",
    ("PLASTIC", "Plastic Fiber") : "SUM_Other_OtherPlasticDebris",
    ("PLASTIC", "Plastic Food Wrappers") : "SUM_Soft_WrapperOrLabel",
    ("PLASTIC", "Plastic Pellet") : "SUM_Other_OtherPlasticDebris",
    ("PLASTIC", "Plastic Utensils") : "SUM_PlasticOrFoamPlatesBowlsCup",
    ("PLASTIC", "Plastic or Foam Fragments") : "SUM_Other_OtherPlasticDebris",
    ("PLASTIC", "Rubber Bands") : "SUM_Other_StrapsTiesBands",
    ("PLASTIC", "Rubber Fragments") : "SUM_Other_OtherPlasticDebris",
    ("PLASTIC", "Rubber Gloves") : "SUM_Other_OtherPlasticDebris",
    ("PLASTIC", "Six-pack rings") : "SUM_Soft_WrapperOrLabel",
    ("PLASTIC", "Strapping Bands") : "SUM_Other_StrapsTiesBands",
    ("PLASTIC", "Straws") : "SUM_Soft_Straw",
    ("PLASTIC", "Tobacco Packaging or Lighters") : "SUM_Hard_Lighter",
    ("PLASTIC", "Toys") : "SUM_Other_OtherPlasticDebris",
    ("RUBBER", "Flip-flops") : "SUM_Other_OtherPlasticDebris",
    ("RUBBER", "Tires") : "SUM_Other_OtherPlasticDebris"
}



In [175]:
transformed_data = []

for item in raw_data.itertuples():
   
    print(item)
    #LIT_PLASTIC_MAPPINGS[(item.tags, item.itemname)]
    

Pandas(Index=0, Litter=1036458, Tags='{bottlecap,plastic}', Location='(-122.134176521,37.401654278)', Country='US', Date='2561-01-30 00:39:52+05')
Pandas(Index=1, Litter=1036624, Tags='{fork,plastic}', Location='(-122.134317937,37.401561979)', Country='US', Date='2561-01-30 00:39:30+05')
Pandas(Index=2, Litter=1036449, Tags='{plastic,wrapper}', Location='(-122.134848444,37.401673876)', Country='US', Date='2561-01-30 00:38:06+05')
Pandas(Index=3, Litter=1025933, Tags='{plastic}', Location='(-122.134343237,37.399733858)', Country='US', Date='2561-01-24 23:47:00+05')
Pandas(Index=4, Litter=1025931, Tags='{tinfoil}', Location='(-122.134468295,37.399795591)', Country='US', Date='2561-01-24 23:46:17+05')
Pandas(Index=5, Litter=1025901, Tags='{tinfoil}', Location='(-122.134003925,37.399765176)', Country='US', Date='2561-01-24 23:46:04+05')
Pandas(Index=6, Litter=1025911, Tags='{tinfoil}', Location='(-122.133821212,37.399905981)', Country='US', Date='2561-01-24 23:45:19+05')
Pandas(Index=7, Li

Pandas(Index=1789, Litter=9196062, Tags='{plastic,wrapper}', Location='(-121.541414246583,47.3925748250414)', Country='US', Date='2020-10-15 23:36:57+05')
Pandas(Index=1790, Litter=9196061, Tags='{plastic}', Location='(-121.541414246583,47.3925748250414)', Country='US', Date='2020-10-15 23:36:56+05')
Pandas(Index=1791, Litter=9196057, Tags='{bottle,plastic}', Location='(-121.541414246583,47.3925748250414)', Country='US', Date='2020-10-15 23:35:36+05')
Pandas(Index=1792, Litter=9197821, Tags='{NULL}', Location='(-96.9980023,28.7937759)', Country='US', Date='2020-10-15 23:34:14+05')
Pandas(Index=1793, Litter=9196056, Tags='{lumber,treated wood,wood}', Location='(-121.54153098294,47.3927344285333)', Country='US', Date='2020-10-15 23:32:58+05')
Pandas(Index=1794, Litter=9196055, Tags='{lumber,treated wood}', Location='(-121.541422768611,47.3925989696734)', Country='US', Date='2020-10-15 23:31:05+05')
Pandas(Index=1795, Litter=9196054, Tags='{lumber,treated wood}', Location='(-121.541425276

Pandas(Index=3789, Litter=9190698, Tags='{NULL}', Location='(-77.730272,38.3263981)', Country='US', Date='2020-10-15 17:54:26+05')
Pandas(Index=3790, Litter=9190709, Tags='{NULL}', Location='(-77.7302666,38.3263964)', Country='US', Date='2020-10-15 17:54:23+05')
Pandas(Index=3791, Litter=9190701, Tags='{NULL}', Location='(-77.7302642,38.3263884)', Country='US', Date='2020-10-15 17:54:13+05')
Pandas(Index=3792, Litter=9190703, Tags='{NULL}', Location='(-77.7302731,38.3263872)', Country='US', Date='2020-10-15 17:54:10+05')
Pandas(Index=3793, Litter=9190699, Tags='{NULL}', Location='(-77.7302961,38.3263934)', Country='US', Date='2020-10-15 17:54:06+05')
Pandas(Index=3794, Litter=9190708, Tags='{NULL}', Location='(-77.7303181,38.3263927)', Country='US', Date='2020-10-15 17:54:04+05')
Pandas(Index=3795, Litter=9190706, Tags='{NULL}', Location='(-77.7303181,38.3263927)', Country='US', Date='2020-10-15 17:54:03+05')
Pandas(Index=3796, Litter=9190710, Tags='{NULL}', Location='(-77.7303476,38.3

Pandas(Index=5788, Litter=9182813, Tags='{NULL}', Location='(-77.7940245,38.3084623)', Country='US', Date='2020-10-15 00:42:41+05')
Pandas(Index=5789, Litter=9182821, Tags='{NULL}', Location='(-77.7940581,38.3085003)', Country='US', Date='2020-10-15 00:42:32+05')
Pandas(Index=5790, Litter=9182815, Tags='{NULL}', Location='(-77.7940133,38.3085003)', Country='US', Date='2020-10-15 00:42:19+05')
Pandas(Index=5791, Litter=9182824, Tags='{NULL}', Location='(-77.7939944,38.3084965)', Country='US', Date='2020-10-15 00:42:12+05')
Pandas(Index=5792, Litter=9182826, Tags='{NULL}', Location='(-77.7939913,38.3085057)', Country='US', Date='2020-10-15 00:42:07+05')
Pandas(Index=5793, Litter=9182827, Tags='{NULL}', Location='(-77.7939907,38.3085093)', Country='US', Date='2020-10-15 00:42:02+05')
Pandas(Index=5794, Litter=9182825, Tags='{NULL}', Location='(-77.7938891,38.308557)', Country='US', Date='2020-10-15 00:41:29+05')
Pandas(Index=5795, Litter=9181843, Tags='{NULL}', Location='(-73.047517603331

Pandas(Index=7665, Litter=9176143, Tags='{NULL}', Location='(-77.8101163,38.3051887)', Country='US', Date='2020-10-14 17:23:38+05')
Pandas(Index=7666, Litter=9176150, Tags='{NULL}', Location='(-77.8101318,38.3052055)', Country='US', Date='2020-10-14 17:23:34+05')
Pandas(Index=7667, Litter=9176148, Tags='{NULL}', Location='(-77.8101391,38.3052092)', Country='US', Date='2020-10-14 17:23:31+05')
Pandas(Index=7668, Litter=9176130, Tags='{NULL}', Location='(-77.8101391,38.3052092)', Country='US', Date='2020-10-14 17:23:30+05')
Pandas(Index=7669, Litter=9176136, Tags='{NULL}', Location='(-77.8101531,38.3052185)', Country='US', Date='2020-10-14 17:23:27+05')
Pandas(Index=7670, Litter=9176129, Tags='{NULL}', Location='(-77.8101683,38.3052156)', Country='US', Date='2020-10-14 17:23:25+05')
Pandas(Index=7671, Litter=9176131, Tags='{NULL}', Location='(-77.8101821,38.3052047)', Country='US', Date='2020-10-14 17:23:23+05')
Pandas(Index=7672, Litter=9176133, Tags='{NULL}', Location='(-77.8101947,38.

...

Pandas(Index=11287, Litter=9145569, Tags='{NULL}', Location='(-87.4564313,37.9723441)', Country='US', Date='2020-10-12 10:08:27+05')
Pandas(Index=11288, Litter=9145567, Tags='{NULL}', Location='(-87.4564313,37.9723441)', Country='US', Date='2020-10-12 10:08:26+05')
Pandas(Index=11289, Litter=9145562, Tags='{NULL}', Location='(-87.4564255,37.9723374)', Country='US', Date='2020-10-12 10:08:26+05')
Pandas(Index=11290, Litter=9145552, Tags='{NULL}', Location='(-87.4564255,37.9723374)', Country='US', Date='2020-10-12 10:08:26+05')
Pandas(Index=11291, Litter=9145560, Tags='{NULL}', Location='(-87.4564255,37.9723374)', Country='US', Date='2020-10-12 10:08:26+05')
Pandas(Index=11292, Litter=9145555, Tags='{NULL}', Location='(-87.4564255,37.9723374)', Country='US', Date='2020-10-12 10:08:25+05')
Pandas(Index=11293, Litter=9145566, Tags='{NULL}', Location='(-87.4564255,37.9723374)', Country='US', Date='2020-10-12 10:08:25+05')
Pandas(Index=11294, Litter=9145561, Tags='{NULL}', Location='(-87.456

Pandas(Index=13286, Litter=9142455, Tags='{NULL}', Location='(-74.4268567488291,40.8598596789323)', Country='US', Date='2020-10-12 03:48:39+05')
Pandas(Index=13287, Litter=9142892, Tags='{bottle,plastic}', Location='(-86.7844853647554,33.5754815617142)', Country='US', Date='2020-10-12 03:48:38+05')
Pandas(Index=13288, Litter=9142376, Tags='{paper}', Location='(-93.9915895276647,29.9840172753017)', Country='US', Date='2020-10-12 03:48:36+05')
Pandas(Index=13289, Litter=9142888, Tags='{plastic}', Location='(-86.7844968671895,33.5754776627777)', Country='US', Date='2020-10-12 03:48:36+05')
Pandas(Index=13290, Litter=9142883, Tags='{paper}', Location='(-86.7845146026962,33.5754660587523)', Country='US', Date='2020-10-12 03:48:34+05')
Pandas(Index=13291, Litter=9142880, Tags='{paper}', Location='(-86.7845171983565,33.575463323871)', Country='US', Date='2020-10-12 03:48:32+05')
Pandas(Index=13292, Litter=9142377, Tags='{paper}', Location='(-93.9915387333315,29.9840267887618)', Country='US', 

Pandas(Index=15286, Litter=9139103, Tags='{NULL}', Location='(-95.4399979860479,29.7036865772956)', Country='US', Date='2020-10-11 22:46:42+05')
Pandas(Index=15287, Litter=9138119, Tags='{NULL}', Location='(-95.2561716177457,30.0552082574275)', Country='US', Date='2020-10-11 22:46:41+05')
Pandas(Index=15288, Litter=9138116, Tags='{hertogjan,plastic}', Location='(-95.2562407684468,30.0551948463824)', Country='US', Date='2020-10-11 22:46:34+05')
Pandas(Index=15289, Litter=9139085, Tags='{NULL}', Location='(-95.4399940465535,29.70370870552)', Country='US', Date='2020-10-11 22:46:30+05')
Pandas(Index=15290, Litter=9138118, Tags='{NULL}', Location='(-95.2588793636476,30.0547634536868)', Country='US', Date='2020-10-11 22:46:28+05')
Pandas(Index=15291, Litter=9138115, Tags='{NULL}', Location='(-95.258893027397,30.0547607884057)', Country='US', Date='2020-10-11 22:46:28+05')
Pandas(Index=15292, Litter=9139080, Tags='{NULL}', Location='(-95.4399525561327,29.7036955878415)', Country='US', Date='

Pandas(Index=17285, Litter=9132701, Tags='{NULL}', Location='(-87.5864222448659,37.976263895867)', Country='US', Date='2020-10-11 19:43:10+05')
Pandas(Index=17286, Litter=9132704, Tags='{NULL}', Location='(-87.5864252251805,37.9762612626938)', Country='US', Date='2020-10-11 19:43:09+05')
Pandas(Index=17287, Litter=9132703, Tags='{NULL}', Location='(-87.5864209070961,37.9762589433282)', Country='US', Date='2020-10-11 19:43:08+05')
Pandas(Index=17288, Litter=9132700, Tags='{NULL}', Location='(-87.5864147783115,37.9762361063855)', Country='US', Date='2020-10-11 19:43:04+05')
Pandas(Index=17289, Litter=9132699, Tags='{NULL}', Location='(-87.5864139728073,37.9762029109051)', Country='US', Date='2020-10-11 19:42:58+05')
Pandas(Index=17290, Litter=9132697, Tags='{NULL}', Location='(-87.5864018679988,37.9761970267898)', Country='US', Date='2020-10-11 19:42:53+05')
Pandas(Index=17291, Litter=9132696, Tags='{NULL}', Location='(-87.5864002747592,37.976191258641)', Country='US', Date='2020-10-11 1

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [177]:
LIT_PLASTIC_MAPPINGS[("CLOTH", "Buoys and floats")]

'SUM_Other_BuoysAndFloats'

In [ ]:


final_data = pd.DataFrame.from_records(transformed_data)
final_data.to_csv(
    os.path.join(PROJECT_DIR, "data", "processed" , "marine-debris-tracker__ec2020-format.csv"), 
    index=False
    )